# 🗺️ Classification k-NN : Haute-Corse ou Corse du Sud ?

## Objectif
Utiliser l'algorithme des **k plus proches voisins (k-NN)** pour déterminer si un point de la carte de Corse se situe en **Haute-Corse (2B)** ou en **Corse du Sud (2A)**, en se basant sur les villages les plus proches.

## Principe
1. On charge les données des villages corses avec leurs coordonnées GPS et leur département
2. On choisit un point sur la carte
3. On calcule les distances entre ce point et tous les villages
4. On identifie les k villages les plus proches
5. On vote : le département majoritaire parmi ces k villages devient la prédiction

## 📦 Installation et imports

In [ ]:
# Installation des bibliothèques nécessaires (si besoin)
import sys
!{sys.executable} -m pip install folium pandas numpy -q

In [ ]:
import pandas as pd
import numpy as np
import folium
from folium.plugins import MarkerCluster
import math
import json
from collections import Counter

## 📊 Chargement des données

In [ ]:
# Charger le fichier CSV
# Remplacez 'villages_corse.csv' par le chemin de votre fichier
df = pd.read_csv('villages_corse.csv', sep='\t', encoding='utf-8')

# Afficher les premières lignes
print(f"Nombre de villages : {len(df)}")
print(f"\nColonnes : {list(df.columns)}")
df.head()

## 🔧 Préparation des données

In [ ]:
def parse_coordinates(point_geo_str):
    """
    Parse la colonne Point_Geo pour extraire latitude et longitude.
    Format attendu : "latitude, longitude"
    Exemple : "41.984099158, 8.798384636"
    """
    try:
        # Séparer par la virgule
        parts = str(point_geo_str).split(',')
        lat = float(parts[0].strip())
        lon = float(parts[1].strip())
        return lat, lon
    except Exception as e:
        print(f"Erreur parsing: {point_geo_str} - {e}")
        return None, None

# Extraire les coordonnées
df[['latitude', 'longitude']] = df['Point_Geo'].apply(
    lambda x: pd.Series(parse_coordinates(x))
)

# Supprimer les lignes sans coordonnées valides
df = df.dropna(subset=['latitude', 'longitude'])

# Simplifier les noms de départements
df['dept_simple'] = df['Code Département'].apply(lambda x: '2A' if str(x) == '2A' else '2B')

print(f"Villages avec coordonnées valides : {len(df)}")
print(f"\nRépartition par département :")
print(df['dept_simple'].value_counts())

df[['Nom français', 'dept_simple', 'latitude', 'longitude']].head(10)

## 📏 Fonction de calcul de distance

Nous utilisons la **formule de Haversine** pour calculer la distance entre deux points GPS sur la surface de la Terre.

In [ ]:
def haversine_distance(lat1, lon1, lat2, lon2):
    """
    Calcule la distance en kilomètres entre deux points GPS.
    Formule de Haversine.
    """
    R = 6371  # Rayon de la Terre en km
    
    # Conversion en radians
    lat1_rad = math.radians(lat1)
    lat2_rad = math.radians(lat2)
    delta_lat = math.radians(lat2 - lat1)
    delta_lon = math.radians(lon2 - lon1)
    
    # Formule de Haversine
    a = math.sin(delta_lat/2)**2 + math.cos(lat1_rad) * math.cos(lat2_rad) * math.sin(delta_lon/2)**2
    c = 2 * math.asin(math.sqrt(a))
    
    return R * c

# Test de la fonction
# Distance entre Ajaccio (41.9267, 8.7369) et Bastia (42.7028, 9.4500)
dist_test = haversine_distance(41.9267, 8.7369, 42.7028, 9.4500)
print(f"Distance Ajaccio-Bastia : {dist_test:.1f} km")

# Test avec Afa et Alando (vos exemples)
afa = df[df['Nom français'] == 'Afa'].iloc[0]
alando = df[df['Nom français'] == 'Alando'].iloc[0]
dist_afa_alando = haversine_distance(afa['latitude'], afa['longitude'], 
                                       alando['latitude'], alando['longitude'])
print(f"Distance Afa-Alando : {dist_afa_alando:.1f} km")

## 🎯 Algorithme k-NN

In [ ]:
def knn_classify(test_lat, test_lon, df, k=5):
    """
    Classifie un point (test_lat, test_lon) en utilisant k-NN.
    
    Retourne :
    - prediction : le département prédit ('2A' ou '2B')
    - neighbors : DataFrame des k plus proches voisins
    - votes : dictionnaire des votes
    """
    # Calculer les distances pour tous les villages
    distances = []
    for idx, row in df.iterrows():
        dist = haversine_distance(test_lat, test_lon, row['latitude'], row['longitude'])
        distances.append({
            'village': row['Nom français'],
            'nom_corse': row['Nom corse'],
            'departement': row['dept_simple'],
            'latitude': row['latitude'],
            'longitude': row['longitude'],
            'distance': dist
        })
    
    # Créer un DataFrame et trier par distance
    dist_df = pd.DataFrame(distances)
    dist_df = dist_df.sort_values('distance')
    
    # Sélectionner les k plus proches
    neighbors = dist_df.head(k)
    
    # Voter
    votes = Counter(neighbors['departement'])
    prediction = votes.most_common(1)[0][0]
    
    return prediction, neighbors, votes

# Test de l'algorithme avec un point au centre de la Corse
test_lat, test_lon = 42.15, 9.05
k = 5

prediction, neighbors, votes = knn_classify(test_lat, test_lon, df, k=k)

print(f"\n🎯 Point de test : ({test_lat}, {test_lon})")
print(f"\nAvec k={k} :")
print(f"Prédiction : {'Corse du Sud (2A)' if prediction == '2A' else 'Haute-Corse (2B)'}")
print(f"Votes : {dict(votes)}")
print(f"\nLes {k} plus proches voisins :")
print(neighbors[['village', 'nom_corse', 'departement', 'distance']])

## 🗺️ Visualisation avec Folium

In [ ]:
def create_map(test_lat=None, test_lon=None, k=5, show_all_villages=False, show_boundaries=False):
    """
    Crée une carte interactive avec Folium.
    
    Paramètres:
    - test_lat, test_lon: coordonnées du point à tester
    - k: nombre de voisins
    - show_all_villages: afficher tous les villages
    - show_boundaries: afficher les frontières des communes (peut être lent)
    """
    # Centre de la Corse
    center_lat = 42.15
    center_lon = 9.05
    
    # Créer la carte
    m = folium.Map(
        location=[center_lat, center_lon],
        zoom_start=9,
        tiles='OpenStreetMap'
    )
    
    # Afficher les frontières des communes (optionnel)
    if show_boundaries:
        print("Affichage des frontières des communes...")
        for idx, row in df.iterrows():
            try:
                zone_geo = json.loads(row['Zone_geo'])
                color = 'red' if row['dept_simple'] == '2A' else 'blue'
                
                folium.GeoJson(
                    zone_geo,
                    style_function=lambda x, color=color: {
                        'fillColor': color,
                        'color': color,
                        'weight': 1,
                        'fillOpacity': 0.1
                    },
                    tooltip=row['Nom français']
                ).add_to(m)
            except:
                pass
    
    # Afficher tous les villages (optionnel)
    if show_all_villages:
        marker_cluster = MarkerCluster().add_to(m)
        
        for idx, row in df.iterrows():
            color = 'red' if row['dept_simple'] == '2A' else 'blue'
            folium.CircleMarker(
                location=[row['latitude'], row['longitude']],
                radius=3,
                color=color,
                fill=True,
                fillColor=color,
                fillOpacity=0.4,
                popup=f"<b>{row['Nom français']}</b><br>{row['Nom corse']}<br>({row['dept_simple']})"
            ).add_to(marker_cluster)
    
    # Si un point de test est fourni
    if test_lat is not None and test_lon is not None:
        # Classification
        prediction, neighbors, votes = knn_classify(test_lat, test_lon, df, k=k)
        
        # Marqueur pour le point de test
        color = 'darkred' if prediction == '2A' else 'darkblue'
        dept_name = 'Corse du Sud (2A)' if prediction == '2A' else 'Haute-Corse (2B)'
        
        folium.Marker(
            location=[test_lat, test_lon],
            popup=f"<b>Point à classifier</b><br>Prédiction : {dept_name}<br>Votes : {dict(votes)}",
            icon=folium.Icon(color=color, icon='star', prefix='fa')
        ).add_to(m)
        
        # Afficher les k plus proches voisins
        for idx, neighbor in neighbors.iterrows():
            # Marqueur pour chaque voisin
            color = 'red' if neighbor['departement'] == '2A' else 'blue'
            folium.Marker(
                location=[neighbor['latitude'], neighbor['longitude']],
                popup=f"<b>{neighbor['village']}</b><br>{neighbor['nom_corse']}<br>{neighbor['departement']}<br>Distance: {neighbor['distance']:.2f} km",
                icon=folium.Icon(color=color, icon='info-sign')
            ).add_to(m)
            
            # Ligne entre le point test et le voisin
            folium.PolyLine(
                locations=[
                    [test_lat, test_lon],
                    [neighbor['latitude'], neighbor['longitude']]
                ],
                color=color,
                weight=2,
                opacity=0.5,
                tooltip=f"{neighbor['distance']:.2f} km"
            ).add_to(m)
    
    # Légende
    legend_html = '''
    <div style="position: fixed; 
                bottom: 50px; right: 50px; width: 220px; height: 130px; 
                background-color: white; border:2px solid grey; z-index:9999; 
                font-size:14px; padding: 10px">
    <p><strong>Légende</strong></p>
    <p><i class="fa fa-circle" style="color:red"></i> Corse du Sud (2A)</p>
    <p><i class="fa fa-circle" style="color:blue"></i> Haute-Corse (2B)</p>
    <p><i class="fa fa-star" style="color:darkred"></i> Point à classifier</p>
    </div>
    '''
    m.get_root().html.add_child(folium.Element(legend_html))
    
    return m

# Créer la carte avec le point de test
map_with_test = create_map(test_lat=42.15, test_lon=9.05, k=5, show_all_villages=False)
map_with_test

## 🔬 Expérimentation : Influence de k

In [ ]:
# Test avec différentes valeurs de k
test_point = (42.15, 9.05)  # Point au centre de la Corse

print(f"Point testé : {test_point}\n")
print(f"{'k':<5} {'Prédiction':<15} {'Votes 2A':<10} {'Votes 2B':<10}")
print("-" * 50)

for k in [1, 3, 5, 7, 9, 15, 21]:
    prediction, neighbors, votes = knn_classify(test_point[0], test_point[1], df, k=k)
    votes_2a = votes.get('2A', 0)
    votes_2b = votes.get('2B', 0)
    dept_name = 'Corse du Sud' if prediction == '2A' else 'Haute-Corse'
    print(f"{k:<5} {dept_name:<15} {votes_2a:<10} {votes_2b:<10}")

## 🎮 Mode interactif : Testez vos propres points !

Modifiez les coordonnées ci-dessous pour tester différents points de la Corse.

**Quelques repères géographiques :**
- Ajaccio : (41.9267, 8.7369)
- Bastia : (42.7028, 9.4500)
- Corte : (42.3062, 9.1509)
- Porto-Vecchio : (41.5914, 9.2795)
- Calvi : (42.5679, 8.7575)

In [ ]:
# === MODIFIEZ CES VALEURS ===
test_latitude = 42.3    # Entre 41.3 (sud) et 43.0 (nord)
test_longitude = 9.15   # Entre 8.5 (ouest) et 9.5 (est)
k_value = 7             # Nombre de voisins
# =============================

prediction, neighbors, votes = knn_classify(test_latitude, test_longitude, df, k=k_value)

print(f"📍 Point : ({test_latitude}, {test_longitude})")
print(f"🔢 k = {k_value}")
print(f"\n🎯 Prédiction : {'Corse du Sud (2A)' if prediction == '2A' else 'Haute-Corse (2B)'}")
print(f"\n📊 Votes : {dict(votes)}")
print(f"\n🏘️ Les {k_value} plus proches villages :")
print(neighbors[['village', 'nom_corse', 'departement', 'distance']].to_string(index=False))

# Afficher la carte
map_interactive = create_map(test_latitude, test_longitude, k=k_value, show_all_villages=False)
map_interactive

## 🌍 Carte complète avec tous les villages

In [ ]:
# Afficher tous les villages de Corse
# Note : cette cellule peut prendre quelques secondes à s'exécuter

map_all = create_map(show_all_villages=True, show_boundaries=False)
map_all

## 🗺️ Carte avec frontières des communes (BONUS)

Cette cellule affiche les frontières réelles des communes. **Attention : cela peut prendre du temps à charger !**

In [ ]:
# Carte avec frontières - peut être lent !
# Décommentez la ligne suivante pour l'exécuter
# map_boundaries = create_map(test_lat=42.15, test_lon=9.05, k=5, show_boundaries=True)
# map_boundaries

## 📈 Visualisation de la frontière de décision

In [ ]:
# Créer une grille de points et classifier chacun
# Cela permet de visualiser la "frontière" selon k-NN

def create_decision_boundary_map(k=5, grid_resolution=40):
    """
    Crée une carte montrant la frontière de décision de k-NN.
    """
    # Limites de la Corse
    lat_min, lat_max = 41.3, 43.0
    lon_min, lon_max = 8.5, 9.6
    
    # Créer une grille
    lats = np.linspace(lat_min, lat_max, grid_resolution)
    lons = np.linspace(lon_min, lon_max, grid_resolution)
    
    m = folium.Map(
        location=[42.15, 9.05],
        zoom_start=8,
        tiles='OpenStreetMap'
    )
    
    # Classifier chaque point de la grille
    print(f"Classification d'une grille de {grid_resolution}x{grid_resolution} points...")
    total = len(lats) * len(lons)
    count = 0
    
    for lat in lats:
        for lon in lons:
            prediction, _, _ = knn_classify(lat, lon, df, k=k)
            color = '#ffcccc' if prediction == '2A' else '#ccccff'
            
            folium.CircleMarker(
                location=[lat, lon],
                radius=4,
                color=color,
                fill=True,
                fillColor=color,
                fillOpacity=0.3,
                weight=0
            ).add_to(m)
            
            count += 1
            if count % 100 == 0:
                print(f"  {count}/{total} points traités ({100*count/total:.1f}%)")
    
    print("Terminé !")
    
    # Ajouter les villages
    for idx, row in df.iterrows():
        color = 'red' if row['dept_simple'] == '2A' else 'blue'
        folium.CircleMarker(
            location=[row['latitude'], row['longitude']],
            radius=2,
            color=color,
            fill=True,
            fillColor=color,
            fillOpacity=0.8,
            popup=row['Nom français']
        ).add_to(m)
    
    return m

# Créer la carte (réduire grid_resolution si c'est trop lent)
print(f"Création de la carte de frontière avec k=5...")
print("Note : cela peut prendre 1-2 minutes...")
boundary_map = create_decision_boundary_map(k=5, grid_resolution=30)
boundary_map

## 💡 Validation de l'algorithme

In [ ]:
# BONUS : Validation croisée
# Tester la précision en utilisant les villages eux-mêmes

def cross_validation(df, k=5, sample_size=100):
    """
    Teste la précision de k-NN en utilisant un échantillon de villages.
    """
    # Prendre un échantillon aléatoire
    sample = df.sample(n=min(sample_size, len(df)), random_state=42)
    
    correct = 0
    total = 0
    errors = []
    
    for idx, row in sample.iterrows():
        # Créer un dataset sans ce village
        df_without = df.drop(idx)
        
        # Classifier ce village
        prediction, neighbors, votes = knn_classify(
            row['latitude'], 
            row['longitude'], 
            df_without, 
            k=k
        )
        
        if prediction == row['dept_simple']:
            correct += 1
        else:
            errors.append({
                'village': row['Nom français'],
                'vrai_dept': row['dept_simple'],
                'prediction': prediction,
                'votes': dict(votes)
            })
        total += 1
    
    accuracy = (correct / total) * 100
    return accuracy, correct, total, errors

print("Test de précision de l'algorithme k-NN...\n")
print("Validation croisée : chaque village est classifié en fonction de ses voisins.\n")

for k in [1, 3, 5, 10, 15]:
    accuracy, correct, total, errors = cross_validation(df, k=k, sample_size=100)
    print(f"k={k:2d} : {accuracy:.1f}% de précision ({correct}/{total} corrects)")

# Afficher quelques erreurs pour k=5
print("\n📋 Exemples d'erreurs avec k=5 :")
_, _, _, errors_k5 = cross_validation(df, k=5, sample_size=100)
if errors_k5:
    for error in errors_k5[:5]:
        print(f"  • {error['village']} : prédit {error['prediction']} (vrai: {error['vrai_dept']}) - votes: {error['votes']}")
else:
    print("  Aucune erreur !")

## 🎓 Questions de réflexion

1. **Influence de k** : Comment la prédiction change-t-elle avec différentes valeurs de k ?

2. **Points frontières** : Trouvez des coordonnées où la classification est ambiguë (votes proches).

3. **Zones problématiques** : Où se situent les villages difficiles à classifier correctement ?

4. **Validité géographique** : Cette méthode respecte-t-elle toujours les vraies frontières administratives ?

5. **Améliorations** : Comment pourrait-on améliorer l'algorithme ?
   - Pondération par distance inverse
   - Prise en compte d'autres critères (altitude, population...)
   - k adaptatif selon la densité de villages

## 💡 Exercices supplémentaires

1. **Trouver la frontière** : Trouvez des points sur la "frontière" k-NN (là où un changement de k change la classification)

2. **Villages isolés** : Identifiez les villages dont le département diffère de leurs k plus proches voisins

3. **Pondération** : Implémentez une version pondérée où les villages plus proches ont plus d'influence

4. **Comparaison** : Comparez la frontière k-NN avec la vraie frontière administrative

In [ ]:
# EXERCICE : Villages "anomaliques"
# Trouver les villages dont les k plus proches voisins sont majoritairement de l'autre département

def find_anomalous_villages(df, k=5):
    """
    Trouve les villages qui seraient mal classifiés par k-NN.
    """
    anomalies = []
    
    for idx, row in df.iterrows():
        # Créer un dataset sans ce village
        df_without = df.drop(idx)
        
        # Classifier ce village
        prediction, neighbors, votes = knn_classify(
            row['latitude'], 
            row['longitude'], 
            df_without, 
            k=k
        )
        
        # Si la prédiction ne correspond pas au vrai département
        if prediction != row['dept_simple']:
            anomalies.append({
                'village': row['Nom français'],
                'nom_corse': row['Nom corse'],
                'vrai_dept': row['dept_simple'],
                'prediction': prediction,
                'votes_2A': votes.get('2A', 0),
                'votes_2B': votes.get('2B', 0),
                'latitude': row['latitude'],
                'longitude': row['longitude']
            })
    
    return pd.DataFrame(anomalies)

print("Recherche des villages 'anomaliques' avec k=5...\n")
anomalies_df = find_anomalous_villages(df, k=5)

print(f"Nombre de villages anomaliques : {len(anomalies_df)}")
print(f"\nVillages qui seraient classifiés dans le mauvais département :\n")
print(anomalies_df[['village', 'nom_corse', 'vrai_dept', 'prediction', 'votes_2A', 'votes_2B']])

# Afficher ces villages sur une carte
if len(anomalies_df) > 0:
    m_anomalies = folium.Map(location=[42.15, 9.05], zoom_start=9)
    
    for idx, row in anomalies_df.iterrows():
        folium.Marker(
            location=[row['latitude'], row['longitude']],
            popup=f"<b>{row['village']}</b><br>Vrai: {row['vrai_dept']}<br>Prédit: {row['prediction']}<br>Votes: {row['votes_2A']}-{row['votes_2B']}",
            icon=folium.Icon(color='orange', icon='exclamation-triangle', prefix='fa')
        ).add_to(m_anomalies)
    
    display(m_anomalies)